In [0]:
import time
start_time = time.time()


In [0]:
gold_csv_path = "/Volumes/workspace/default/sentiment_analysis/final_ml_predictions.csv"

df = (
    spark.read
    .option("header", "true")
    .option("inferSchema", "true")
    .csv(gold_csv_path)
)

df.display()
df.printSchema()


id text created_at username user_id language retweet_count like_count reply_count quote_count impression_count hashtags mentions source is_retweet is_reply in_reply_to_user_id conversation_id user_followers_count user_following_count user_verified user_location possibly_sensitive clean_text sentiment_label emotion_label 1.95E18 Agent every development say quality throughout beautiful. #DataBreach 11-01-2025 18:16 @fjohnson 958070516 en 4 5 2 0 43 #DataBreach null Twitter for iPhone false false null 6.99E18 59 1634 false East William false agent every development say quality throughout beautiful. databreach positive joy 3.56E18 Night respond red information last everything. #CVE @blakeerik 07-09-2024 15:01 @jpeterson 819895579 en 2 10 2 0 44 #CVE @blakeerik TweetDeck false false null 2.15E18 12401 1005 false Port Matthew false night respond red information last everything. cve positive fear 3.67E18 Here grow gas enough analysis least by. #InfoSec #CyberSecurity #MFA 27-03-2025 10:09 @smiller 918490409 en 2 13 0 0 46 #InfoSec, #CyberSecurity, #MFA null TweetDeck false false null 9.64E18 9514 1995 false Barbaraland false here grow gas enough analysis least by. infosec cybersecurity mfa positive fear 7.31E18 Product significant world talk term herself. Player half have decide environment view possible. #MFA #CVE @amandasanchez @ogray 18-10-2024 11:26 @gabriellecameron 825070419 en 3 4 0 0 55 #MFA, #CVE @amandasanchez, @ogray Android false true null 7.62E18 1329 428 false East Lydiamouth false product significant world talk term herself. player half have decide environment view possible. mfa cve positive fear 4.95E18 Environment decision wall then fire pretty how trip learn enter east. Much section investment on gun young catch. #SOC #SOC #Phishing @ddavis @hernandezernest 06-03-2025 06:33 @ycarlson 428953029 en 1 6 3 0 55 #SOC, #SOC, #Phishing @ddavis, @hernandezernest Twitter Web App false false 1.7187936E8 7.28E18 28089 920 false Carlsonmouth false environment decision wall then fire pretty how trip learn enter east. much section investment on gun young catch. soc soc phishing positive fear 7.29E18 Edge network wall quite boy those seem shoulder future fall citizen about. #MFA @teresa28 @harrellkenneth 03-03-2025 02:51 @ericfarmer 806348900 en 0 8 1 0 65 #MFA @teresa28, @harrellkenneth Twitter for iPhone false false null 9.96E18 4950 1316 false New Mariotown false edge network wall quite boy those seem shoulder future fall citizen about. mfa positive fear 1.01E18 Patch for Credential Stuffing vulnerability released. Upon these story film. #SOC @allenashley @millertodd 23-12-2024 22:40 @spenceamanda 524736385 en 6 10 1 0 40 #SOC @allenashley, @millertodd TweetDeck false true null 1.79E18 2340 1681 false null false patch for credential stuffing vulnerability released. upon these story film. soc negative fear 9.89E18 Campaign little near enter their institution deep. #Hacking #Phishing #SOC @jenniferross @samuel87 21-09-2024 06:07 @wrightcaleb 579164766 en 2 9 0 2 49 #Hacking, #Phishing, #SOC @jenniferross, @samuel87 Android false false null 5.16E18 5464 296 false New Angelashire false campaign little near enter their institution deep. hacking phishing soc negative fear 3.11E18 According remain arrive attack all form method everything. Democrat car very number line six space. #CVE @clintonhopkins @rodney70 17-08-2024 07:27 @brownjessica 33829406 es 4 7 2 1 53 #CVE @clintonhopkins, @rodney70 Android false true null 6.31E18 750 387 false null false according remain arrive attack all form method everything. democrat car very number line six space. cve positive fear 1.56E18 Backup systems engaged after brute force. Eat couple large instead. #CyberSecurity #MFA #MFA @steven17 @williamsyvette 06-11-2024 10:25 @novaksara 364423393 es 4 10 0 3 60 #CyberSecurity, #MFA, #MFA @steven17, @williamsyvette Twitter for iPhone false false null 1.7E18 30482 1698 false null false backup systems engaged after brute force. eat couple large instead. cyb

root
 |-- id: double (nullable = true)
 |-- text: string (nullable = true)
 |-- created_at: string (nullable = true)
 |-- username: string (nullable = true)
 |-- user_id: integer (nullable = true)
 |-- language: string (nullable = true)
 |-- retweet_count: integer (nullable = true)
 |-- like_count: integer (nullable = true)
 |-- reply_count: integer (nullable = true)
 |-- quote_count: integer (nullable = true)
 |-- impression_count: integer (nullable = true)
 |-- hashtags: string (nullable = true)
 |-- mentions: string (nullable = true)
 |-- source: string (nullable = true)
 |-- is_retweet: boolean (nullable = true)
 |-- is_reply: boolean (nullable = true)
 |-- in_reply_to_user_id: double (nullable = true)
 |-- conversation_id: double (nullable = true)
 |-- user_followers_count: integer (nullable = true)
 |-- user_following_count: integer (nullable = true)
 |-- user_verified: boolean (nullable = true)
 |-- user_location: string (nullable = true)
 |-- possibly_sensitive: boolean (nullab

In [0]:
from pyspark.sql.functions import col, to_date, trim

gold_base_df = (
    df
    .withColumn(
        "date",
        to_date(col("created_at"), "dd-MM-yyyy HH:mm")
    )
    .withColumn("hashtags", trim(col("hashtags")))
)


In [0]:
%sql
DROP TABLE IF EXISTS default.gold_daily_hashtag;


gold_daily_hashtag

In [0]:
from pyspark.sql.functions import explode, split, count

gold_daily_hashtag = (
    gold_base_df
    .withColumn("hashtag", explode(split(col("hashtags"), ",")))
    .filter(col("hashtag").isNotNull() & (col("hashtag") != ""))
    .groupBy("date", "hashtag")
    .agg(count("*").alias("hashtag_count"))
)

gold_daily_hashtag.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("default.gold_daily_hashtag")


gold_daily_sentiment

In [0]:
gold_daily_sentiment = (
    gold_base_df
    .groupBy("date", col("sentiment_label").alias("sentiment"))
    .agg(count("*").alias("sentiment_count"))
)

gold_daily_sentiment.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("default.gold_daily_sentiment")


In [0]:
gold_hashtag_trends = (
    gold_base_df
    .withColumn("hashtag", explode(split(col("hashtags"), ",")))
    .filter(col("hashtag").isNotNull() & (col("hashtag") != ""))
    .groupBy("hashtag")
    .agg(count("*").alias("total_count"))
    .orderBy(col("total_count").desc())
)

gold_hashtag_trends.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("default.gold_hashtag_trends")


In [0]:
from pyspark.sql.functions import sum, round

sentiment_counts = (
    gold_base_df
    .groupBy(col("sentiment_label").alias("sentiment"))
    .agg(count("*").alias("count"))
)

total_count = sentiment_counts.agg(sum("count")).collect()[0][0]

gold_sentiment_percentage = (
    sentiment_counts
    .withColumn(
        "percentage",
        round((col("count") / total_count) * 100, 2)
    )
)

gold_sentiment_percentage.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("default.gold_sentiment_percentage")


In [0]:
from pyspark.sql.functions import sum as _sum

gold_top_users = (
    gold_base_df
    .groupBy("username", "user_id")
    .agg(
        _sum("retweet_count").alias("total_retweets"),
        _sum("like_count").alias("total_likes"),
        _sum("reply_count").alias("total_replies")
    )
    .withColumn(
        "engagement_score",
        col("total_retweets") +
        col("total_likes") +
        col("total_replies")
    )
    .orderBy(col("engagement_score").desc())
)

gold_top_users.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("default.gold_top_users")


In [0]:
from pyspark.sql.functions import (
    col, explode, split, count, trim,
    to_timestamp, to_date
)

gold_df = (
    gold_base_df
    .withColumn("hashtag", explode(split(col("hashtags"), ",")))
    .withColumn("hashtag", trim(col("hashtag")))
    .filter(col("hashtag").isNotNull() & (col("hashtag") != ""))
    
    .withColumn(
        "created_ts",
        to_timestamp(col("created_at"), "dd-MM-yyyy HH:mm")
    )
    .withColumn("date", to_date(col("created_ts")))
    .groupBy("date", "hashtag")
    .agg(count("*").alias("count"))
)

gold_df.write \
    .format("delta") \
    .mode("overwrite") \
    .saveAsTable("gold_trending_topics")


In [0]:
end_time = time.time()
print(f"Total notebook runtime: {(end_time - start_time)/60:.2f} minutes")


Total notebook runtime: 1.13 minutes
